$$V(x,y)=-V_0\cos^2\left(k_Lx\right)\cos^2\left(k_Ly\right)-\frac{V_1}{4}\left(\cos(2k_Lx)-\cos(2k_Ly)\right)^2$$

$$V_n=-\frac1{16}\left(V_0\begin{pmatrix}
0&0&0&0&0\\
0&1&2&1&0\\
0&2&4&2&0\\
0&1&2&1&0\\
0&0&0&0&0\end{pmatrix}+V_1\begin{pmatrix}
0&0&1&0&0\\
0&-2&0&-2&0\\
1&0&4&0&1\\
0&-2&0&-2&0\\
0&0&1&0&0\end{pmatrix}\right)$$

In [1]:
import numpy as np
import tensorflow as tf

import plotly.graph_objects as go

In [2]:
num_quasimomenta = 99

max_momentum_site = 5
num_momentum_sites = (2*max_momentum_site + 1) ** 2

In [3]:
quasimomentum = np.mgrid[0:2:num_quasimomenta*1j,
                         0:2:num_quasimomenta*1j].reshape(2,-1).T

momentum_site = np.mgrid[-max_momentum_site:max_momentum_site+1:1,
                         -max_momentum_site:max_momentum_site+1:1].reshape(2,-1).T

momentum = 2*momentum_site + quasimomentum[:, np.newaxis]
kinetic = np.linalg.norm(momentum, axis=-1)**2

momentum_site_change = momentum_site[:, np.newaxis] - momentum_site
max_momentum_site_change = 2 * max_momentum_site

In [4]:
def render_momentum_site_potential(depths):
    return -1/16 * (
        depths[0] * np.array([
            [0, 0, 0, 0, 0],
            [0, 1, 2, 1, 0],
            [0, 2, 4, 2, 0],
            [0, 1, 2, 1, 0],
            [0, 0, 0, 0, 0]
        ]) +
        depths[1] * np.array([
            [ 0,  0, +1,  0,  0],
            [ 0, -2,  0, -2,  0],
            [+1,  0, +4,  0, +1],
            [ 0, -2,  0, -2,  0],
            [ 0,  0, +1,  0,  0],
        ])
    )

In [5]:
def spatial_from_momentum_site_potential(momentum_site_potential, num_points=100):
    return np.real(np.fft.fft2(np.fft.ifftshift(np.pad(momentum_site_potential, 100))))

In [6]:
def compute_dispersion(momentum_site_potential):
    max_potential_momentum_site = (momentum_site_potential.shape[0] - 1) // 2

    potential = np.pad(momentum_site_potential, max_momentum_site_change - max_potential_momentum_site)[
        momentum_site_change[:, :, 0] + max_momentum_site_change,
        momentum_site_change[:, :, 1] + max_momentum_site_change,
    ]

    energy = tf.linalg.diag(kinetic) + potential[np.newaxis, ...]

    dispersion = tf.reshape(tf.linalg.eigvalsh(energy), (num_quasimomenta, num_quasimomenta, num_momentum_sites))

    return dispersion

In [9]:
momentum_site_potential = render_momentum_site_potential(np.array([1, 1]))
spatial_potential = spatial_from_momentum_site_potential(momentum_site_potential)

figure = go.Figure(data=[go.Surface(z=np.tile(spatial_potential, (2, 2)))])
figure.update_layout(autosize=False, width=750, height=750)
figure.show()

In [10]:
depths = np.array([1, 1.094]) * 40

momentum_site_potential = render_momentum_site_potential(depths)

dispersion = compute_dispersion(momentum_site_potential)

figure = go.Figure(data=[go.Surface(z=dispersion[:, :, band], showscale=False) for band in range(0, 3)])
figure.update_layout(autosize=False, width=750, height=750, 
)
figure.show()